# Ground Motion Prediction 

## Import pygmm module

In [1]:
import pygmm

## Import ObsPy module
https://anaconda.org/conda-forge/obspy

In [2]:

from obspy.geodetics.base import gps2dist_azimuth

import obspy as ob
print("# obspy version = ",ob.__version__)

# obspy version =  1.2.2


In [7]:
import pandas as pd
print("# pandas version = ",pd.__version__)


# pandas version =  1.0.4


## Computer JB distance
This example uses hypocenteral distance between the epicenter and terget area.


In [8]:
def cal_jb_dist(evla, evlo, stla, stlo):
    #baz = gps2dist_azimuth(source_latitude, source_longitude, station_latitude, station_longitude)
    baz = gps2dist_azimuth(evla, evlo, stla, stlo)

    #print('Epicentral distance [m]: ', baz[0])
    #print('Theoretical azimuth [deg]: ', baz[1])
    #print('Theoretical backazimuth [deg]: ', baz[2])

    dist_jb = baz[0]/1000 # convert to m -> km
    #print("# dist_jb = ", dist_jb)
    return dist_jb
          

## Input parameters
this would depend on the target locations

In [9]:
stname = "regionA" # this is used for the output file
# target location
stla = 37.87352 # latitude of the target area # this example use BK.BRK station
stlo = -122.26099 # longitude of the target area # this example use BK.BRK station
# vs30
v_s30 = 500 # m/s find this vs30 from grd file 
# https://github.com/usgs/earthquake-global_vs30/tree/master/California/California_Vs30_7p5c.grd
# region. 
region = "california" # need for BSSA14


### option. if you want to save results for each target region
event_pgv_fi = stname+"_BSSA14.csv"

## Read event_focal csv file


In [10]:
event_focal_fi = "bayarea_center_m3_500km_focal.csv"
event_focal_fi = "test_eq_focal.csv" # two events only
event_focal_fi = "bayarea_center_m3_500km_focal_redo.csv"

event_focal_df = pd.read_csv(event_focal_fi ,   
                       sep=",")

In [11]:
print(event_focal_df)

                          time   latitude   longitude  depth   mag magType  \
0     2020-12-01T23:47:05.591Z  38.167500 -118.081300   5.60  4.30      ml   
1     2020-12-01T23:43:08.516Z  38.172700 -118.070300   4.80  4.30      ml   
2     2020-12-01T23:39:55.064Z  38.172200 -118.050400   8.00  3.20      ml   
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
4     2020-12-01T23:32:56.573Z  38.163700 -118.083700   5.00  5.10      ml   
...                        ...        ...         ...    ...   ...     ...   
2127  2018-01-11T00:15:13.680Z  36.156333 -120.229833  11.36  3.14      ml   
2128  2018-01-07T19:01:00.490Z  40.398667 -125.244667  29.45  4.52      mw   
2129  2018-01-07T01:31:11.150Z  34.420000 -120.001500   2.26  3.78      mw   
2130  2018-01-04T10:39:37.730Z  37.855167 -122.256833  12.31  4.38      mw   
2131  2017-12-31T19:49:06.270Z  40.484667 -123.390000  30.44  3.76      mw   

              id Rupture_type mechanism  strike     dip    rake

In [12]:
# may be more better way...
event_focal_df['PGA'] = event_focal_df['rake']
event_focal_df['PGV'] = event_focal_df['rake']
event_focal_df['dist_jb'] = event_focal_df['rake']


In [13]:
#for eventid in event_df['id']:
for i, eventid in enumerate(event_focal_df['id']):

    print("# i = ",i)
    print("# evenid = ", eventid)
    # compute JB distnace. You can replace it by your approach
    dist_jb = cal_jb_dist(event_focal_df['latitude'][i], event_focal_df['longitude'][i], stla, stlo)
    print("# dist_jb = ", dist_jb)
    event_focal_df.loc[i, ('dist_jb')] = dist_jb

    ### BSSA2014
    scenario = pygmm.Scenario(mag=event_focal_df['mag'][i], dist_jb=dist_jb, v_s30=v_s30, region=region, mechanism=event_focal_df['mechanism'][i])
    m = pygmm.BooreStewartSeyhanAtkinson2014(scenario)
    #print("# PGA (g) = ", m.pga)
    #print("# PGV (cm/s) = ", m.pgv)
    event_focal_df.loc[i, ('PGA')] = m.pga
    event_focal_df.loc[i, ('PGV')] = m.pgv


# i =  0
# evenid =  nn00787133
# dist_jb =  368.42603999525517
# i =  1
# evenid =  nn00787124
# dist_jb =  369.42633876133806
# i =  2
# evenid =  nn00787116
# dist_jb =  371.16245991272143
# i =  3
# evenid =  nn00787110
# dist_jb =  368.12801517450526
# i =  4
# evenid =  nn00787105
# dist_jb =  368.1885087266349
# i =  5
# evenid =  nn00787091
# dist_jb =  307.80761946358984
# i =  6
# evenid =  nc73491170
# dist_jb =  308.94110927210136
# i =  7
# evenid =  ci39481463
# dist_jb =  493.8759803944533
# i =  8
# evenid =  nn00786813
# dist_jb =  376.3942085534729
# i =  9
# evenid =  nn00786787
# dist_jb =  352.15024414161144
# i =  10
# evenid =  ci39480223
# dist_jb =  483.6777806784417
# i =  11
# evenid =  nc73488761
# dist_jb =  325.57335300821853
# i =  12
# evenid =  nc73487351
# dist_jb =  309.9365103008313
# i =  13
# evenid =  nn00786014
# dist_jb =  391.1484462134791
# i =  14
# evenid =  nn00786004
# dist_jb =  389.27404862982166
# i =  15
# evenid =  nn00785639
# dist_j

# i =  68
# evenid =  nc73464086
# dist_jb =  153.79767097071422
# i =  69
# evenid =  nc73463746
# dist_jb =  56.92273401716224
# i =  70
# evenid =  nc73463646
# dist_jb =  57.249839068947786
# i =  71
# evenid =  nn00775722
# dist_jb =  379.96156350808764
# i =  72
# evenid =  ci38701098
# dist_jb =  492.2661186434241
# i =  73
# evenid =  nn00775128
# dist_jb =  384.5888033280393
# i =  74
# evenid =  nn00774930
# dist_jb =  369.94855900697814
# i =  75
# evenid =  nn00774584
# dist_jb =  385.46152680096117
# i =  76
# evenid =  nn00774492
# dist_jb =  390.2811480914469
# i =  77
# evenid =  ci38693130
# dist_jb =  411.0634420037635
# i =  78
# evenid =  nn00773931
# dist_jb =  378.7789262921038
# i =  79
# evenid =  nc73457811
# dist_jb =  240.31207433586272
# i =  80
# evenid =  nc73457786
# dist_jb =  240.7082409050503
# i =  81
# evenid =  ci38683938
# dist_jb =  411.1713770451798
# i =  82
# evenid =  ci38683930
# dist_jb =  411.4814937464548
# i =  83
# evenid =  ci38683914
#

# i =  129
# evenid =  nn00763446
# dist_jb =  397.13247525598865
# i =  130
# evenid =  nn00763220
# dist_jb =  397.10802375687774
# i =  131
# evenid =  nn00763107
# dist_jb =  378.2716611411419
# i =  132
# evenid =  nn00762911
# dist_jb =  380.5981970034371
# i =  133
# evenid =  nc73432571
# dist_jb =  124.21746196331934
# i =  134
# evenid =  ci38605954
# dist_jb =  413.60578952642663
# i =  135
# evenid =  nn00762581
# dist_jb =  372.30602369381825
# i =  136
# evenid =  nn00762576
# dist_jb =  371.799655583167
# i =  137
# evenid =  nn00762498
# dist_jb =  392.2184414517374
# i =  138
# evenid =  nn00762457
# dist_jb =  381.95598339481484
# i =  139
# evenid =  ci38603762
# dist_jb =  411.06132801646385
# i =  140
# evenid =  nc73429346
# dist_jb =  157.02106332354825
# i =  141
# evenid =  ci38599882
# dist_jb =  435.9978714904292
# i =  142
# evenid =  nc73428141
# dist_jb =  310.51223409082615
# i =  143
# evenid =  nn00761307
# dist_jb =  389.50133984410417
# i =  144
# eve

 177
# evenid =  ci39266159
# dist_jb =  411.0265179572268
# i =  178
# evenid =  ci39496504
# dist_jb =  413.79186319441436
# i =  179
# evenid =  ci39496160
# dist_jb =  410.97147053674513
# i =  180
# evenid =  nc73415886
# dist_jb =  108.59772208631824
# i =  181
# evenid =  ci39495128
# dist_jb =  410.8502117044861
# i =  182
# evenid =  nn00752967
# dist_jb =  396.4688214452157
# i =  183
# evenid =  ci39494672
# dist_jb =  411.0807833621888
# i =  184
# evenid =  ci39494264
# dist_jb =  416.1229529158463
# i =  185
# evenid =  ci39494128
# dist_jb =  410.70996796782015
# i =  186
# evenid =  ci39494120
# dist_jb =  411.317323692305
# i =  187
# evenid =  ci39494088
# dist_jb =  414.5111561107556
# i =  188
# evenid =  ci39494008
# dist_jb =  415.44898208669997
# i =  189
# evenid =  ci39493968
# dist_jb =  414.8094405175993
# i =  190
# evenid =  ci39493944
# dist_jb =  412.2463472551871
# i =  191
# evenid =  nn00752366
# dist_jb =  373.6734740625214
# i =  192
# evenid =  ci39

 214
# evenid =  nn00750141
# dist_jb =  392.22031214733676
# i =  215
# evenid =  nn00750130
# dist_jb =  391.4639578961369
# i =  216
# evenid =  nn00749736
# dist_jb =  389.7298576192211
# i =  217
# evenid =  ci39483592
# dist_jb =  447.365138455811
# i =  218
# evenid =  nc73410846
# dist_jb =  67.3549716478148
# i =  219
# evenid =  ci39481424
# dist_jb =  445.5491438175199
# i =  220
# evenid =  nn00749012
# dist_jb =  384.7932262375858
# i =  221
# evenid =  nn00748811
# dist_jb =  370.49896813928683
# i =  222
# evenid =  nn00748659
# dist_jb =  377.2291635586667
# i =  223
# evenid =  nn00748633
# dist_jb =  378.93997314977696
# i =  224
# evenid =  nn00747938
# dist_jb =  385.3106424351347
# i =  225
# evenid =  nn00747919
# dist_jb =  354.5951195257146
# i =  226
# evenid =  nn00747912
# dist_jb =  354.71580748173955
# i =  227
# evenid =  nn00747897
# dist_jb =  354.59014601962906
# i =  228
# evenid =  ci39477608
# dist_jb =  461.19763169879445
# i =  229
# evenid =  nn00

...

# i =  1895
# evenid =  ci37222404
# dist_jb =  485.44697306393925
# i =  1896
# evenid =  ci37259588
# dist_jb =  474.7290345213075
# i =  1897
# evenid =  ci37256196
# dist_jb =  487.9991005925107
# i =  1898
# evenid =  ci37222396
# dist_jb =  485.60179305092936
# i =  1899
# evenid =  us70004a0n
# dist_jb =  487.08357897683476
# i =  1900
# evenid =  ci37421941
# dist_jb =  489.6151107254054
# i =  1901
# evenid =  ci38443199
# dist_jb =  481.9352959739866
# i =  1902
# evenid =  ci37259580
# dist_jb =  487.601556040012
# i =  1903
# evenid =  ci37218996
# dist_jb =  493.225824582874
# i =  1904
# evenid =  ci37222364
# dist_jb =  489.29265180758796
# i =  1905
# evenid =  ci37222372
# dist_jb =  489.70990750926654
# i =  1906
# evenid =  ci37222380
# dist_jb =  482.46871879152707
# i =  1907
# evenid =  ci37255980
# dist_jb =  480.8422370781167
# i =  1908
# evenid =  ci37218988
# dist_jb =  488.8136766438467
# i =  1909
# evenid =  ci37222356
# dist_jb =  493.8018438813935
# i = 

# i =  1962
# evenid =  nc73166830
# dist_jb =  333.09704411373343
# i =  1963
# evenid =  nc73166680
# dist_jb =  333.06802498851687
# i =  1964
# evenid =  nc73166265
# dist_jb =  114.59143314002048
# i =  1965
# evenid =  nc73164840
# dist_jb =  114.9892300820639
# i =  1966
# evenid =  nc73164200
# dist_jb =  109.16451679070524
# i =  1967
# evenid =  us70003453
# dist_jb =  458.0294082701633
# i =  1968
# evenid =  nc73161470
# dist_jb =  277.5498925711791
# i =  1969
# evenid =  nn00681228
# dist_jb =  320.04493870049953
# i =  1970
# evenid =  nc73157855
# dist_jb =  341.7194446753711
# i =  1971
# evenid =  nc73155640
# dist_jb =  376.35842830539207
# i =  1972
# evenid =  nc73155340
# dist_jb =  332.01582370760343
# i =  1973
# evenid =  nn00680709
# dist_jb =  426.0974726216463
# i =  1974
# evenid =  ci38277999
# dist_jb =  453.9705332982178
# i =  1975
# evenid =  us1000jd0s
# dist_jb =  467.98730369620296
# i =  1976
# evenid =  nc73147611
# dist_jb =  119.17341169936908
#

# i =  2017
# evenid =  nn00668094
# dist_jb =  260.27042387779085
# i =  2018
# evenid =  nc73118836
# dist_jb =  363.25902648548106
# i =  2019
# evenid =  nc73116386
# dist_jb =  271.95858715608136
# i =  2020
# evenid =  nc73113891
# dist_jb =  391.24927491394635
# i =  2021
# evenid =  nc73112376
# dist_jb =  400.6877070214147
# i =  2022
# evenid =  nc73109341
# dist_jb =  21.00443094584801
# i =  2023
# evenid =  nc73109266
# dist_jb =  158.8413049336314
# i =  2024
# evenid =  nc73109006
# dist_jb =  194.04268263169254
# i =  2025
# evenid =  ci38351080
# dist_jb =  419.5130133787779
# i =  2026
# evenid =  nc73105366
# dist_jb =  156.0780195552179
# i =  2027
# evenid =  nc73105346
# dist_jb =  157.70805044187583
# i =  2028
# evenid =  nc73105336
# dist_jb =  157.55881319325263
# i =  2029
# evenid =  nc73105296
# dist_jb =  157.3072400505157
# i =  2030
# evenid =  nc73105281
# dist_jb =  156.22565750552099
# i =  2031
# evenid =  nc73105276
# dist_jb =  156.79246363779546
#

# i =  2073
# evenid =  nc73024816
# dist_jb =  316.35520567727633
# i =  2074
# evenid =  nc73023166
# dist_jb =  21.15646952578309
# i =  2075
# evenid =  nc73021190
# dist_jb =  160.37372450898383
# i =  2076
# evenid =  nc73016870
# dist_jb =  88.02788305970485
# i =  2077
# evenid =  nc73016050
# dist_jb =  9.178289525215108
# i =  2078
# evenid =  nc73016111
# dist_jb =  475.9532739673225
# i =  2079
# evenid =  nc73014286
# dist_jb =  112.4685443673501
# i =  2080
# evenid =  nc73014276
# dist_jb =  114.03106779548555
# i =  2081
# evenid =  nc73012946
# dist_jb =  408.3047911038059
# i =  2082
# evenid =  nc73012146
# dist_jb =  388.589742938543
# i =  2083
# evenid =  nc73010506
# dist_jb =  164.8630376474305
# i =  2084
# evenid =  nc73008716
# dist_jb =  24.018479049499692
# i =  2085
# evenid =  nc73002966
# dist_jb =  330.0274257391985
# i =  2086
# evenid =  nc73002681
# dist_jb =  228.017658460443
# i =  2087
# evenid =  nc73000196
# dist_jb =  65.01381979377118
# i =  2

 2126
# evenid =  nc72954970
# dist_jb =  303.1421948404792
# i =  2127
# evenid =  nc72952250
# dist_jb =  262.6473940954605
# i =  2128
# evenid =  nc72950451
# dist_jb =  380.9183832804325
# i =  2129
# evenid =  ci37848263
# dist_jb =  433.77887937822527
# i =  2130
# evenid =  nc72948801
# dist_jb =  2.069680835484531
# i =  2131
# evenid =  nc72946846
# dist_jb =  305.8533161082878


In [14]:
#event_focal_df['id']

## show dist_jb <= 20 km

In [15]:
# dist_jb < 20
event_focal_df[event_focal_df['dist_jb'] <= 20]


time   latitude   longitude  depth   mag magType  \
776   2019-10-16T02:11:58.540Z  37.948167 -122.061833  14.30  3.24      ml   
778   2019-10-15T05:33:42.810Z  37.938000 -122.057000  13.97  4.46      mw   
2002  2019-01-17T14:11:07.620Z  37.848500 -122.238333  10.52  3.39      ml   
2003  2019-01-16T12:42:09.100Z  37.846000 -122.248000  10.18  3.43      mw   
2077  2018-05-15T02:18:35.000Z  37.805333 -122.202000   8.77  3.45      mw   
2130  2018-01-04T10:39:37.730Z  37.855167 -122.256833  12.31  4.38      mw   

              id Rupture_type mechanism  strike   dip   rake focal_source  \
776   nc73292585           SS        SS   340.0  85.0  170.0           FM   
778   nc73291880           SS        SS   160.0  85.0 -180.0           FM   
2002  nc73133716         SS-N        SS   135.0  60.0 -170.0           FM   
2003  nc73133456         SS-N        SS    50.0  80.0  -30.0           FM   
2077  nc73016050           SS        SS   240.0  85.0   10.0           FM   
2130  nc72948801         SS-N        SS    60.0  90.0  -40.0           FM   

           PGA       PGV    dist_jb  
776   0.001495  0.031745  19.374545  
778   0.014059  0.489694  19.314753  
2002  0.011892  0.243538   3.418642  
2003  0.012945  0.271046   3.261439  
2077  0.005713  0.132614   9.178290  
2130  0.066819  2.112995   2.069681

## show PGV >= 0.1 cm/s

In [16]:
event_focal_df[event_focal_df['PGV'] >= 1e-1]

time   latitude   longitude  depth   mag magType  \
593   2020-05-15T11:03:27.176Z  38.168900 -117.849700   2.70  6.50      ml   
778   2019-10-15T05:33:42.810Z  37.938000 -122.057000  13.97  4.46      mw   
936   2019-07-16T20:11:01.470Z  37.818667 -121.756833  12.38  4.31      mw   
1762  2019-07-06T03:19:53.040Z  35.769500 -117.599333   8.00  7.10      mw   
1912  2019-07-04T17:33:49.000Z  35.705333 -117.503833  10.50  6.40      mw   
2002  2019-01-17T14:11:07.620Z  37.848500 -122.238333  10.52  3.39      ml   
2003  2019-01-16T12:42:09.100Z  37.846000 -122.248000  10.18  3.43      mw   
2077  2018-05-15T02:18:35.000Z  37.805333 -122.202000   8.77  3.45      mw   
2130  2018-01-04T10:39:37.730Z  37.855167 -122.256833  12.31  4.38      mw   

              id Rupture_type mechanism  strike    dip    rake focal_source  \
593   nn00725272         SS-N        SS  168.46  66.74 -167.11           MT   
778   nc73291880           SS        SS  160.00  85.00 -180.00           FM   
936   nc73225421         SS-N        SS  350.00  55.00 -150.00           FM   
1762  ci38457511           SS        SS  160.00  84.00 -165.00           FM   
1912  ci38443183           SS        SS  139.00  85.00 -178.00           FM   
2002  nc73133716         SS-N        SS  135.00  60.00 -170.00           FM   
2003  nc73133456         SS-N        SS   50.00  80.00  -30.00           FM   
2077  nc73016050           SS        SS  240.00  85.00   10.00           FM   
2130  nc72948801         SS-N        SS   60.00  90.00  -40.00           FM   

           PGA       PGV     dist_jb  
593   0.000875  0.229283  388.690549  
778   0.014059  0.489694   19.314753  
936   0.003321  0.117469   44.789384  
1762  0.000677  0.277139  476.878450  
1912  0.000299  0.117220  487.945223  
2002  0.011892  0.243538    3.418642  
2003  0.012945  0.271046    3.261439  
2077  0.005713  0.132614    9.178290  
2130  0.066819  2.112995    2.069681

### Save result (Optional)

In [17]:
event_pgv_df = pd.DataFrame({ 'time' : event_focal_df['time'],
                        'latitude' : event_focal_df['latitude'],
                        'longitude' :event_focal_df['longitude'],
                        'depth' : event_focal_df['longitude'],
                        'mag' : event_focal_df['mag'],
                        'magType' : event_focal_df['magType'],
                        'Rupture_type' : event_focal_df['Rupture_type'], 
                        'mechanism' : event_focal_df['mechanism'], 
                        'strike' : event_focal_df['strike'],
                        'dip' : event_focal_df['dip'],
                        'rake' : event_focal_df['rake'],
                        'focal_source' : event_focal_df['focal_source'],
                        'PGV' : event_focal_df['PGV'],
                        'PGA' : event_focal_df['PGA'],
                        'dist_jb' : event_focal_df['dist_jb'],
                        'id' : event_focal_df['id'] }  )

event_pgv_df.to_csv(event_pgv_fi, columns=['time','PGV','PGA','dist_jb','latitude','longitude','depth','mag','magType','id','Rupture_type','mechanism','strike','dip','rake','focal_source'], index=False, sep=',')

